In [1]:
import urllib.request, json 
import pandas as pd
from io import StringIO

url_covid_france='https://www.data.gouv.fr/fr/datasets/r/63352e38-d353-4b54-bfd1-f1b3ee1cabd7'

with urllib.request.urlopen(url_covid_france) as url:
    data=pd.read_table(StringIO(url.read().decode()),sep=";")
    
data.tail()

dep  sexe        jour  hosp  rea  rad  dc
27571  974     1  2020-06-16    18    2   64   1
27572  974     2  2020-06-16     4    1   65   0
27573  976     0  2020-06-16    40   10  306  25
27574  976     1  2020-06-16    22    4  139  18
27575  976     2  2020-06-16    18    6  162   7

In [2]:
maxdate=max(data["jour"])
d=data[(data["jour"]==maxdate) & (data["sexe"]==0)]

In [3]:
import geopandas as gpd
import numpy as np
import pandas as pd

shapefile='https://datanova.laposte.fr/explore/dataset/geoflar-departements-2015/download/?format=shp&timezone=Europe/Berlin&lang=fr'

gdf = gpd.read_file(shapefile)[['nom_dept','code_dept','geometry',]]

gdf.head()

nom_dept code_dept  \
0           HAUTS-DE-SEINE        92   
1                    MARNE        51   
2              DEUX-SEVRES        79   
3  ALPES-DE-HAUTE-PROVENCE        04   
4                   CANTAL        15   

                                            geometry  
0  POLYGON ((2.22040 48.92061, 2.22054 48.92071, ...  
1  POLYGON ((3.70465 49.20066, 3.70062 49.20124, ...  
2  POLYGON ((-0.77317 46.84036, -0.77424 46.84073...  
3  POLYGON ((5.63114 44.15058, 5.63300 44.15030, ...  
4  POLYGON ((2.36463 45.37468, 2.36380 45.37648, ...

In [4]:
depnum=pd.to_numeric(gdf["code_dept"],errors='coerce').replace(np.nan,0,regex=True).astype(int)
gdf2=gdf[((depnum>0) & (depnum<100)) | (gdf["code_dept"]=="2A") | (gdf["code_dept"]=="2B")]
gdf2.head()

nom_dept code_dept  \
0           HAUTS-DE-SEINE        92   
1                    MARNE        51   
2              DEUX-SEVRES        79   
3  ALPES-DE-HAUTE-PROVENCE        04   
4                   CANTAL        15   

                                            geometry  
0  POLYGON ((2.22040 48.92061, 2.22054 48.92071, ...  
1  POLYGON ((3.70465 49.20066, 3.70062 49.20124, ...  
2  POLYGON ((-0.77317 46.84036, -0.77424 46.84073...  
3  POLYGON ((5.63114 44.15058, 5.63300 44.15030, ...  
4  POLYGON ((2.36463 45.37468, 2.36380 45.37648, ...

In [5]:
merged=gdf2.merge(d[["dep","dc"]], left_on = 'code_dept', right_on = 'dep', how = 'left')

merged.sort_values("dep",inplace=True)
jdata=merged.to_json()
merged.head()

nom_dept code_dept  \
70                      AIN        01   
61                    AISNE        02   
15                   ALLIER        03   
3   ALPES-DE-HAUTE-PROVENCE        04   
25             HAUTES-ALPES        05   

                                             geometry dep   dc  
70  POLYGON ((4.80255 46.15643, 4.80238 46.15689, ...  01  101  
61  POLYGON ((3.12039 49.70573, 3.12028 49.70726, ...  02  272  
15  POLYGON ((2.53665 46.51970, 2.53711 46.52006, ...  03   39  
3   POLYGON ((5.63114 44.15058, 5.63300 44.15030, ...  04   13  
25  POLYGON ((5.95112 44.75962, 5.95166 44.76019, ...  05   18

In [6]:
from bokeh.io import output_notebook, show, output_file
from bokeh.plotting import figure
from bokeh.models import GeoJSONDataSource, LinearColorMapper, ColorBar, HoverTool
from bokeh.palettes import brewer

#Input GeoJSON source that contains features for plotting.
geosource = GeoJSONDataSource(geojson = jdata)

#Define a sequential multi-hue color palette.
palette = brewer['YlGnBu'][8]
palette = palette[::-1]

hover = HoverTool(tooltips = [ ('Département','@nom_dept (@dep)'),('Décès totaux', '@dc')])

#Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
color_mapper = LinearColorMapper(palette = palette, low = 0, high=1000)
#Define custom tick labels for color bar.
#tick_labels = {'0': '0%', '5': '5%', '10':'10%', '15':'15%', '20':'20%'}#, '25':'25%', '30':'30%','35':'35%', '40': '>40%'}

#Create color bar. 
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=8,width = 500, height = 20,
border_line_color=None,location = (0,0), orientation = 'horizontal')#, major_label_overrides = tick_labels)

#Create figure object.
p = figure(title = 'France métropole, nb décès au '+str(maxdate), plot_height = 900 , plot_width = 950, tools = [hover])#, toolbar_location = None)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

#Add patch renderer to figure. 
p.patches('xs','ys', source = geosource,fill_color = {'field' :'dc', 'transform' : color_mapper},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)

#Specify figure layout.
p.add_layout(color_bar, 'below')

#Display figure inline in Jupyter Notebook.
output_notebook()

#Display figure.
show(p)

Loading BokehJS ...